# Set IP

In [4]:
IP_INDY = "192.168.0.99"   # IP of Indy
IP_XAVIER = "192.168.0.74" # IP Address of Xavier (same as Indy if you are using IndyEye built in CB)

# IndyEye communication
* 자세한 사항은 주석 참조

In [5]:
import time
import socket
import sys
import json
import numpy as np

##
# @class NumpyEncoder
# @brief Numpy array encoder for communication
class NumpyEncoder(json.JSONEncoder):
    def default(self, obj):
        if isinstance(obj, np.ndarray):
            return obj.tolist()
        return json.JSONEncoder.default(self, obj)

TASK_PORT = 2002    # default IndyEye Task Server Port
custom_dat_len = 32 # default custom data length
TASK_DETECT = 0     # detect command
TASK_RETRIEVE = 1   # no-detect, retrieve results one-by-one, with Select module ON RETRIEVE Option
TASK_RESET = 2      # not used now
TASK_GETLIST = 3    # get class list

##
# @brief indyeye communication function
# @param cmd        command id, 0~3
# @param cls        index of target class to detect. 0: ALL, 1~: index of class
# @param pose_cmd   end-effector pose, [x,y,z,u,v,w] (unit: m, deg)
# @param robot_ip   ip address of the robot, for multi-robot use
# @return     {
#              'Tbe' : pick pose of end-effector in base coordinates
#              'Tbt' : pick pose of tool point in base coordinates
#              'Tbo' : detected object pose in base coordinates
#              'class_detect' : detected class index. 0: not assigned, 1~: index of class
#              'tool_idx' : selected tool index
#              'STATE' : 0-OK, 1-NG
#              'custom_dat' : 32 custom values array
#              'class_list' : list of available class, only for TASK_GETLIST command
#             }
def run_command(cmd,cls,pose_cmd=None, robot_ip=None, host=IP_XAVIER, port=TASK_PORT, **kwargs):
    sock = socket.socket(socket.AF_INET,
                         socket.SOCK_STREAM) # SOCK_STREAM is TCP socket
    
    try:
        sock.connect((host,port))
        sdict = {'command': int(cmd), 'class_tar': int(cls), }
        if pose_cmd is not None:
            sdict['pose_cmd']= pose_cmd
        if robot_ip is not None:
            sdict['robot_ip']= robot_ip
        sdict.update(kwargs)
        sjson = json.dumps(sdict, cls=NumpyEncoder)
        sbuff = sjson.encode()
        sock.send(sbuff)
        print('sent: ',sjson)
        
        rbuff = sock.recv(1024)
        rjson = "".join(map(chr, rbuff))
        rdict = json.loads(rjson)
        print('received: ', rdict)
        
    finally:
        sock.close()
    return rdict

# Inspection
* **[WARNING]** 아래 명령 방식은 단순 검사에만 사용합니다. 물체 위치 감지에는 로봇 자세가 필요합니다.
* **[WARNING]** This is only for inspection. For object pose detection, robot pose is required.

In [30]:
class_list = run_command(TASK_GETLIST, 0)["class_list"]

sent:  {"command": 3, "class_tar": 0}
received:  {'class_list': ['left', 'right'], 'STATE': 0}


In [31]:
res = run_command(TASK_DETECT, 0)
if res["STATE"]>0:
    print("NG")
else:
    print("PASS")
    print("detected: {}".format(class_list[res["class_detect"]-1] if res["class_detect"]>0 else "undefined"))

sent:  {"command": 0, "class_tar": 0}
received:  {'Tbe': [0.3624437749385834, -0.186542809009552, 0.7879899740219116, -179.99277380138722, -0.08371998578000293, 179.99121961154887], 'Tbt': [0, 0, 0, 0, 0, 0], 'Tbo': [0, 0, 0, 0, 0, 0], 'class_detect': 0, 'tool_idx': 0, 'STATE': 1, 'custom_dat': [0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0]}
NG


# Prepare Indy
* **[WARNING]** IndyDCP 중복 연결을 방지하기 위해 아래에서 연결하기 전 IndyEye 앱의 로봇 연결을 끊어야 함
* **[WARNING]** Disconnect connection to Indy in the IndyEye APP, as DCP server can handle only single client.

In [32]:
import os
import sys
sys.path.append(os.path.dirname(os.getcwd()))
from Controller.indydcp_client import IndyDCPClient

In [33]:
indy = IndyDCPClient(server_ip=IP_INDY, robot_name="NRMK-Indy7")

#### 현재 로봇 자세 받기 - 물체 위치를 얻기 위해 카메라가 부착된 로봇의 현재 위치가 필요
#### Getting current robot pose - To get exact object pose, we need to know th pose of the robot on which the camera is attached.

In [34]:
indy.connect()
pos_cur = indy.get_task_pos()
indy.disconnect()

Connect: Server IP (192.168.0.99)


#### 로봇 자세와 함께 감지 수행
#### Detect object with the acquired robot pose
* **Camera** 모듈에서 캘리브레이션 파일을 선택 한 경우, 선택한 캘리브레이션을 수행한 로봇 IP를 robot_ip에 넘겨 주어야 해당 카메라의 영상을 바탕으로 인식을 수행합니다.
* If you selected calibration file in the **Camera** module, you need to pass the ip of the robot that you used during that calibration to the robot_ip parameter. The camera is selected based on the robot_ip.

In [38]:
res = run_command(TASK_DETECT, 1, pose_cmd=pos_cur)
if res["STATE"]>0:
    print("NG")
else:
    print("PASS")
    print("detected: {}".format(class_list[res["class_detect"]-1] if res["class_detect"]>0 else "undefined"))
    print("pick pose: {}".format(res["Tbe"]))

sent:  {"command": 0, "class_tar": 1}
received:  {'Tbe': [0.36545366048812866, 0.124594546854496, 0.3849917948246002, 178.20159297283797, -8.907879472841836, -179.97276847506234], 'Tbt': [0.35229694843292236, 0.12725584208965302, 0.3010583817958832, 178.20159297283797, -8.907879472841836, -179.97276847506234], 'Tbo': [0.35229694843292236, 0.12725584208965302, 0.3010583817958832, 178.20159297283797, -8.907879472841836, -179.97276847506234], 'class_detect': 0, 'tool_idx': 0, 'STATE': 0, 'custom_dat': [0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0]}
PASS
detected: undefined
pick pose: [0.36545366048812866, 0.124594546854496, 0.3849917948246002, 178.20159297283797, -8.907879472841836, -179.97276847506234]


#### 픽 자세로 이동
#### Move to pick pose
 - IndyEye에서 **Griper** 모듈 설정이 완료된 경우에만 픽 자세를 정상적으로 리턴합니다. 설정이 안됐면 Tbe는 로봇의 현재 자세를 리턴함.
 - The Pick pose can be returned only when the **Gripper** module is set in the IndyEye. If not, the current robot pose will be stored in Tbe.

In [39]:
indy.connect()
pos_cur = indy.task_move_to(res['Tbe'])
indy.disconnect()

Connect: Server IP (192.168.0.99)


## 홈 복귀
## Return to home

In [40]:
indy.connect()
pos_cur = indy.go_home()
indy.disconnect()

Connect: Server IP (192.168.0.99)
